In [2]:
#RAW IMPORTS

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
data = pd.read_csv('ufo.csv')


C:\Users\Chiara\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3071: DtypeWarning: Columns (5) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [3]:
#CLEANING AND PARSING

data["date-time"]=data["date-time"].str.replace("24:00","00:00",regex=False)
data["date-time"]=pd.to_datetime(data["date-time"], errors='raise')

data["report-date"]=pd.to_datetime(data["report-date"], errors='raise')

data["latitude"]=data["latitude"].astype(float, errors='raise')
data["longitude"]=data["longitude"].astype(float, errors='raise')

data["sec-duration"]=data[data["duration"].str.match("(.*min.*)")]["duration"].str.extract("(\d+)").astype(float)*60
data["sec-duration"] = data["sec-duration"].fillna(0)

data["sec-duration-2"]=data[data["duration"].str.match("(.*sec.*)")]["duration"].str.extract("(\d+)").astype(float)
data["sec-duration-2"] = data["sec-duration-2"].fillna(0)

data["sec-duration-3"]=data[data["duration"].str.match("(.*h.+)")]["duration"].str.extract("(\d+)").astype(float)*3600
data["sec-duration-3"] = data["sec-duration-3"].fillna(0)

data["sec-duration"] = data["sec-duration-2"]+data["sec-duration"]+data["sec-duration-3"]

#Ancora circa 5000 durate da pulire

#data

date-time                  city state country     shape  \
0     1949-10-10 20:30:00            san marcos    tx      us  cylinder   
1     1949-10-10 21:00:00          lackland afb    tx     NaN     light   
2     1955-10-10 17:00:00  chester (uk/england)   NaN      gb    circle   
3     1956-10-10 21:00:00                  edna    tx      us    circle   
4     1960-10-10 20:00:00               kaneohe    hi      us     light   
...                   ...                   ...   ...     ...       ...   
80326 2013-09-09 21:15:00             nashville    tn      us     light   
80327 2013-09-09 22:00:00                 boise    id      us    circle   
80328 2013-09-09 22:00:00                  napa    ca      us     other   
80329 2013-09-09 22:20:00                vienna    va      us    circle   
80330 2013-09-09 23:00:00                edmond    ok      us     cigar   

      unknown_column    duration  \
0               2700  45 minutes   
1               7200     1-2 hrs   
2                 20  20 seconds   
3                 20    1/2 hour   
4                900  15 minutes   
...              ...         ...   
80326            600  10 minutes   
80327           1200  20 minutes   
80328           1200        hour   
80329              5   5 seconds   
80330           1020  17 minutes   

                                             description report-date  \
0      This event took place in early fall around 194...  2004-04-27   
1      1949 Lackland AFB&#44 TX.  Lights racing acros...  2005-12-16   
2      Green/Orange circular disc over Chester&#44 En...  2008-01-21   
3      My older brother and twin sister were leaving ...  2004-01-17   
4      AS a Marine 1st Lt. flying an FJ4B fighter/att...  2004-01-22   
...                                                  ...         ...   
80326  Round from the distance/slowly changing colors...  2013-09-30   
80327  Boise&#44 ID&#44 spherical&#44 20 min&#44 10 r...  2013-09-30   
80328                                       Napa UFO&#44  2013-09-30   
80329  Saw a five gold lit cicular craft moving fastl...  2013-09-30   
80330  2 witnesses 2  miles apart&#44 Red &amp; White...  2013-09-30   

        latitude   longitude  sec-duration  sec-duration-2  sec-duration-3  
0      29.883056  -97.941111        2700.0             0.0             0.0  
1      29.384210  -98.581082        3600.0             0.0          3600.0  
2      53.200000   -2.916667          20.0            20.0             0.0  
3      28.978333  -96.645833        3600.0             0.0          3600.0  
4      21.418056 -157.803611         900.0             0.0             0.0  
...          ...         ...           ...             ...             ...  
80326  36.165833  -86.784444         600.0             0.0             0.0  
80327  43.613611 -116.202500        1200.0             0.0             0.0  
80328  38.297222 -122.284444           0.0             0.0             0.0  
80329  38.901111  -77.265556           5.0             5.0             0.0  
80330  35.652778  -97.477778        1020.0             0.0             0.0  

[80331 rows x 14 columns]

In [ ]:
data_s=data.sample(8000)
fig = px.scatter_geo(data_s,
                    lat=data_s["latitude"],
                    lon=data_s["longitude"],
                    opacity=0.1,
                    title="All-time sightings map"
                    )
fig.show()

In [ ]:
data_by_year=data.groupby(data["date-time"].dt.year).count()
fig2 = px.line(data_by_year, x=data_by_year.index, y="date-time", title='Sightings by year', labels={"index": "Year", "date-time":"Sightings"})
fig2.show()


In [ ]:
dataSampled=data;
year = dataSampled["date-time"].dt.year.unique()

year = np.sort(year)
year


In [ ]:
plotData = []
layout = dict(
    title = 'Sightings per year',
    # showlegend = False,
    autosize = False,
    width = 1000,
    height = 3000,
    hovermode = False,
    legend = dict(
        x=0.7,
        y=-0.1,
        bgcolor="rgba(255, 255, 255, 0)",
        font = dict( size=11 ),
    )
)
for i in range(len(year)):
    geo_key = 'geo'+str(i+1) if i != 0 else 'geo'
    lons = list(dataSampled[ dataSampled['date-time'].dt.year == year[i] ]['longitude'])
    lats = list(dataSampled[ dataSampled['date-time'].dt.year == year[i] ]['latitude'])
    # Walmart store data
    plotData.append(
        dict(
            type = 'scattergeo',
            showlegend=False,
            lon = lons,
            lat = lats,
            geo = geo_key,
            name = int(year[i]),
            marker = dict(
                color = "rgb(0, 0, 255)",
                opacity = 0.5
                
            )
        )
    )
    # Year markers
    plotData.append(
        dict(
            type = 'scattergeo',
            showlegend = False,
            lon = [-78],
            lat = [47],
            geo = geo_key,
            text = [year[i]],
            mode = 'text',
        )
    )
    layout[geo_key] = dict(
        scope = 'usa',
        showland = True,
        landcolor = 'rgb(229, 229, 229)',
        showcountries = False,
        domain = dict( x = [], y = [] ),
        subunitcolor = "rgb(255, 255, 255)",
    )

z = 0
COLS = 4
ROWS = 23
for y in reversed(range(ROWS)):
    for x in range(COLS):
        if z > len(year)-1:
            break
        geo_key = 'geo'+str(z+1) if z != 0 else 'geo'
        layout[geo_key]['domain']['x'] = [float(x)/float(COLS), float(x+1)/float(COLS)]
        layout[geo_key]['domain']['y'] = [float(y)/float(ROWS), float(y+1)/float(ROWS)]
        z=z+1
        
    

layout



In [ ]:
fig = go.Figure(data=plotData, layout=layout)
#fig.update_layout(width=800)
#fig.show()

In [ ]:
#forme ufo
formeData = data
formeData = formeData.groupby("shape").count()
formeData = formeData[formeData["date-time"]>10]
formeData = formeData.sort_values("date-time")
formeData


In [ ]:
fig = px.bar(formeData, 
             y=formeData.index, 
             x=formeData["date-time"],
            labels={'shape':'shape','date-time': 'sightings'},
            title = "UFO shape" )
fig.show()

In [ ]:
#densità avvistamenti

denData = data
denData["lat-mod"]= denData["latitude"] -denData["latitude"]%0.001
denData["lon-mod"]= denData["longitude"] -denData["longitude"]%0.001
graph=denData.groupby(["lat-mod", "lon-mod"]).count()
graph.index.get_level_values("lat-mod")

In [ ]:



fig = px.density_mapbox(graph, lat=graph.index.get_level_values("lat-mod"), lon=graph.index.get_level_values("lon-mod"), z='date-time', radius=15,
                        center=dict(lat=39, lon=-98), zoom=2.5,
                        mapbox_style="stamen-terrain")
fig.show()

In [37]:
#tempo tra avvistamento e segnalazione
tempo = data
tempo["time-between"]=tempo["report-date"].dt.year- tempo["date-time"].dt.year

tempo


date-time                  city state country     shape  \
0     1949-10-10 20:30:00            san marcos    tx      us  cylinder   
1     1949-10-10 21:00:00          lackland afb    tx     NaN     light   
2     1955-10-10 17:00:00  chester (uk/england)   NaN      gb    circle   
3     1956-10-10 21:00:00                  edna    tx      us    circle   
4     1960-10-10 20:00:00               kaneohe    hi      us     light   
...                   ...                   ...   ...     ...       ...   
80326 2013-09-09 21:15:00             nashville    tn      us     light   
80327 2013-09-09 22:00:00                 boise    id      us    circle   
80328 2013-09-09 22:00:00                  napa    ca      us     other   
80329 2013-09-09 22:20:00                vienna    va      us    circle   
80330 2013-09-09 23:00:00                edmond    ok      us     cigar   

      unknown_column    duration  \
0               2700  45 minutes   
1               7200     1-2 hrs   
2                 20  20 seconds   
3                 20    1/2 hour   
4                900  15 minutes   
...              ...         ...   
80326            600  10 minutes   
80327           1200  20 minutes   
80328           1200        hour   
80329              5   5 seconds   
80330           1020  17 minutes   

                                             description report-date  \
0      This event took place in early fall around 194...  2004-04-27   
1      1949 Lackland AFB&#44 TX.  Lights racing acros...  2005-12-16   
2      Green/Orange circular disc over Chester&#44 En...  2008-01-21   
3      My older brother and twin sister were leaving ...  2004-01-17   
4      AS a Marine 1st Lt. flying an FJ4B fighter/att...  2004-01-22   
...                                                  ...         ...   
80326  Round from the distance/slowly changing colors...  2013-09-30   
80327  Boise&#44 ID&#44 spherical&#44 20 min&#44 10 r...  2013-09-30   
80328                                       Napa UFO&#44  2013-09-30   
80329  Saw a five gold lit cicular craft moving fastl...  2013-09-30   
80330  2 witnesses 2  miles apart&#44 Red &amp; White...  2013-09-30   

        latitude   longitude  sec-duration  sec-duration-2  sec-duration-3  \
0      29.883056  -97.941111        2700.0             0.0             0.0   
1      29.384210  -98.581082        3600.0             0.0          3600.0   
2      53.200000   -2.916667          20.0            20.0             0.0   
3      28.978333  -96.645833        3600.0             0.0          3600.0   
4      21.418056 -157.803611         900.0             0.0             0.0   
...          ...         ...           ...             ...             ...   
80326  36.165833  -86.784444         600.0             0.0             0.0   
80327  43.613611 -116.202500        1200.0             0.0             0.0   
80328  38.297222 -122.284444           0.0             0.0             0.0   
80329  38.901111  -77.265556           5.0             5.0             0.0   
80330  35.652778  -97.477778        1020.0             0.0             0.0   

       time-between  
0                55  
1                56  
2                53  
3                48  
4                44  
...             ...  
80326             0  
80327             0  
80328             0  
80329             0  
80330             0  

[80331 rows x 15 columns]

In [38]:
#x=tempo["date-time"].dt.date
#y=tempo["report-date"]
tfig = go.Figure([go.Scatter(x=tempo['date-time'], y=tempo['time-between'])])
tfig.show()